In [0]:
# Read CSV from Volume
df = spark.read.csv("/Volumes/test/default/raw_data/Extended_Employee_Performance_and_Productivity_Data.csv", header=True)

# Write to Unity Catalog table
df.write.saveAsTable("test.default.employee_data")

In [0]:
%sql
CREATE VOLUME workspace.default.raw_data;

In [0]:
%sql
SELECT * FROM test.default.employee_data LIMIT 20;

Employee_ID Department Gender Age Job_Title Hire_Date Years_At_Company Education_Level Performance_Score Monthly_Salary Work_Hours_Per_Week Projects_Handled Overtime_Hours Sick_Days Remote_Work_Frequency Team_Size Training_Hours Promotions Employee_Satisfaction_Score Resigned 1 IT Male 55 Specialist 2022-01-19 08:03:05.556036 2 High School 5 6750.0 33 32 22 2 0 14 66 0 2.63 False 2 Finance Male 29 Developer 2024-04-18 08:03:05.556036 0 High School 5 7500.0 34 34 13 14 100 12 61 2 1.72 False 3 Finance Male 55 Specialist 2015-10-26 08:03:05.556036 8 High School 3 5850.0 37 27 6 3 50 10 1 0 3.17 False 4 Customer Support Female 48 Analyst 2016-10-22 08:03:05.556036 7 Bachelor 2 4800.0 52 10 28 12 100 10 0 1 1.86 False 5 Engineering Female 36 Analyst 2021-07-23 08:03:05.556036 3 Bachelor 2 4800.0 38 11 29 13 100 15 9 1 1.25 False 6 IT Male 43 Manager 2016-08-14 08:03:05.556036 8 High School 3 7800.0 46 31 8 0 100 15 95 0 2.77 False 7 IT Male 37 Technician 2023-08-28 08:03:05.556036 1 Bachelor 5 5250.0 55 20 29 2 0 16 27 0 4.46 False 8 Engineering Female 55 Engineer 2014-10-27 08:03:05.556036 9 Bachelor 2 7200.0 42 46 7 8 100 7 64 0 2.09 False 9 Marketing Female 55 Technician 2023-06-29 08:03:05.556036 1 High School 2 4200.0 51 23 21 14 0 1 0 1 1.44 False 10 Engineering Female 45 Consultant 2016-12-23 08:03:05.556036 7 Bachelor 1 6050.0 41 33 2 6 75 4 53 2 2.93 False 11 Customer Support Male 52 Engineer 2019-11-26 08:03:05.556036 4 Bachelor 3 7800.0 38 1 5 0 25 4 90 1 2.34 False 12 Customer Support Male 27 Technician 2015-02-19 08:03:05.556036 9 Bachelor 5 5250.0 39 13 2 13 25 5 88 0 1.96 False 13 HR Male 51 Technician 2019-07-04 08:03:05.556036 5 Bachelor 4 4900.0 31 11 16 1 75 7 17 2 2.13 False 14 Engineering Male 27 Analyst 2014-10-14 08:03:05.556036 9 Bachelor 4 5600.0 33 30 5 13 25 4 26 1 1.46 False 15 Finance Male 46 Analyst 2023-03-11 08:03:05.556036 1 Master 1 4400.0 33 49 13 1 100 13 37 1 2.22 False 16 Customer Support Male 26 Developer 2023-04-19 08:03:05.556036 1 High School 2 6000.0 33 41 9 13 50 3 46 1 2.42 False 17 Operations Male 29 Engineer 2019-09-21 08:03:05.556036 4 Bachelor 2 7200.0 43 26 29 12 0 6 76 2 3.15 False 18 Sales Other 28 Developer 2022-11-08 08:03:05.556036 1 High School 3 6500.0 47 36 6 12 75 12 54 0 1.19 False 19 Customer Support Other 56 Developer 2015-10-01 08:03:05.556036 8 Bachelor 1 5500.0 57 9 24 1 75 1 36 0 1.12 False 20 Finance Male 23 Technician 2015-05-08 08:03:05.556036 9 High School 2 4200.0 52 0 9 1 0 5 66 0 3.91 False

In [0]:
%sql
-- Create Silver Table with Liquid Clustering for high performance
CREATE TABLE IF NOT EXISTS test.default.employee_performance_silver
CLUSTER BY (Department, Education_Level) -- Modern replacement for partitioning
AS
SELECT
    -- Create a unique surrogate key if one doesn't exist
    cast(Employee_ID as STRING) as employee_id,
    cast(Department as STRING) as department,
    cast(Gender as STRING) as gender,
    cast(Education_Level as STRING) as education_level,
    -- Handle numeric types and nulls
    coalesce(cast(Performance_Score as FLOAT), 0) as productivity_score,
    coalesce(cast(Overtime_Hours as FLOAT), 0) as overtime_hours,
    cast(Years_At_Company as INT) as tenure_years,
    cast(Remote_Work_Frequency as FLOAT) as remote_freq,
    -- Audit Metadata
    current_timestamp() as _ingested_at,
    'Kaggle_Source' as _source_sys
FROM test.default.employee_data
WHERE Employee_ID IS NOT NULL;

-- Add a Constraint (Professional touch)
ALTER TABLE test.default.employee_performance_silver 
ADD CONSTRAINT productivity_range CHECK (productivity_score >= 0 AND productivity_score <= 100);

In [0]:
%sql
-- VIEW 1: Executive Summary (Aggregated KPIs)
CREATE OR REPLACE VIEW test.default.gold_executive_summary AS
SELECT 
    department,
    count(employee_id) as head_count,
    round(avg(productivity_score), 2) as avg_dept_productivity,
    round(avg(remote_freq), 2) as avg_remote_adoption,
    sum(overtime_hours) as total_ot_hours
FROM test.default.employee_performance_silver
GROUP BY department;

-- VIEW 2: Burnout Risk Analysis (Using Window Functions)
-- This identifies people working 20% more OT than their department average
CREATE OR REPLACE VIEW test.default.gold_burnout_risk AS
WITH DeptAvg AS (
    SELECT *,
           avg(overtime_hours) OVER(PARTITION BY department) as dept_avg_ot
    FROM test.default.employee_performance_silver
)
SELECT 
    employee_id,
    department,
    productivity_score,
    overtime_hours,
    dept_avg_ot,
    CASE 
        WHEN overtime_hours > (dept_avg_ot * 1.2) AND productivity_score > 85 THEN 'High Performer / High Risk'
        WHEN overtime_hours > (dept_avg_ot * 1.2) THEN 'High Risk'
        ELSE 'Stable'
    END as risk_status
FROM DeptAvg;

-- VIEW 3: Efficiency & Prediction Gap
-- Note: Replace 'predicted_score' with your actual ML prediction column name
CREATE OR REPLACE VIEW test.default.gold_performance_gap AS
SELECT 
    employee_id,
    department,
    tenure_years,
    productivity_score as actual_score,
    -- Simulating a prediction if you haven't run AutoML yet; 
    -- replace this with your actual ML table join later
    (productivity_score * 0.95) as predicted_score, 
    (productivity_score - (productivity_score * 0.95)) as prediction_variance
FROM test.default.employee_performance_silver;

In [0]:
%sql
CREATE VOLUME test.default.mlflow_tmp;

In [0]:
import mlflow
import mlflow.spark
from pyspark.ml import Pipeline
from pyspark.ml.feature import VectorAssembler, StringIndexer, StandardScaler
from pyspark.ml.regression import RandomForestRegressor
from pyspark.ml.evaluation import RegressionEvaluator
from mlflow.models import infer_signature

# 1. Start MLflow Run
mlflow.set_registry_uri("databricks-uc") # Use Unity Catalog for model governance
model_name = "test.default.productivity_prediction_model"

with mlflow.start_run(run_name="Employee_Productivity_RF"):
    # 2. Prepare Data
    df = spark.read.table("test.default.employee_performance_silver")
    train_df, test_df = df.randomSplit([0.8, 0.2], seed=42)

    # 3. Feature Engineering Stages
    # Convert Department (string) to numerical index
    indexer = StringIndexer(inputCol="department", outputCol="dept_index", handleInvalid="keep")
    
    # Combine all features into a single vector
    feature_cols = ["dept_index", "overtime_hours", "tenure_years", "remote_freq"]
    assembler = VectorAssembler(inputCols=feature_cols, outputCol="unscaled_features")
    
    # Scale features (Standard practice for better model performance)
    scaler = StandardScaler(inputCol="unscaled_features", outputCol="features")

    # 4. Define Model (Random Forest Regressor)
    rf = RandomForestRegressor(featuresCol="features", labelCol="productivity_score", numTrees=10)

    # 5. Build and Train Pipeline
    pipeline = Pipeline(stages=[indexer, assembler, scaler, rf])
    model = pipeline.fit(train_df)

    # 6. Log Model and Metrics
    predictions = model.transform(test_df)
    evaluator = RegressionEvaluator(labelCol="productivity_score", predictionCol="prediction", metricName="rmse")
    rmse = evaluator.evaluate(predictions)
    
    signature = infer_signature(train_df.toPandas(), predictions.select("prediction").toPandas())
    mlflow.log_metric("rmse", rmse)
    mlflow.spark.log_model(model, "model", registered_model_name=model_name, dfs_tmpdir="/Volumes/test/default/mlflow_tmp/", signature=signature)
    
    print(f"Model trained with RMSE: {rmse}")

/databricks/python/lib/python3.12/site-packages/mlflow/types/utils.py:452: UserWarning: Hint: Inferred schema contains integer column(s). Integer columns in Python cannot represent missing values. If your input data contains missing values at inference time, it will be encoded as floats and will cause a schema enforcement error. The best way to avoid this problem is to infer the model schema based on a realistic data sample (training dataset) that includes missing values. Alternatively, you can declare integer columns as doubles (float64) whenever these columns may have missing values. See `Handling Integers With Missing Values <https://www.mlflow.org/docs/latest/models.html#handling-integers-with-missing-values>`_ for more details.
  warnings.warn(
2026/01/14 21:42:13 WARNING mlflow.utils.requirements_utils: Found pyspark version (4.0.0+databricks.connect.17.2.2) contains a local version label (+databricks.connect.17.2.2). MLflow logged a pip requirement for this package as 'pyspark==

Uploading artifacts:   0%|          | 0/44 [00:00<?, ?it/s]

Successfully registered model 'test.default.productivity_prediction_model'.


Uploading artifacts:   0%|          | 0/44 [00:00<?, ?it/s]

Created version '1' of model 'test.default.productivity_prediction_model'.


Model trained with RMSE: 1.4200575830613325


In [0]:
import os
import mlflow

# Set UC volume path for MLflow SparkML model loading
os.environ["MLFLOW_DFS_TMP"] = "/Volumes/test/default/mlflow_tmp/"

# Load the model from Unity Catalog using a valid alias
model_name = "test.default.productivity_prediction_model"
model_uri = f"models:/{model_name}@champion"  # Use the actual alias assigned in Model Registry
model = mlflow.pyfunc.load_model(model_uri=model_uri)

# Load Silver data as Pandas DataFrame (select only features used for training)
silver_df = spark.read.table("test.default.employee_performance_silver")
pdf = silver_df.toPandas()

# Apply the model
pdf["predicted_score"] = model.predict(pdf)

# Add back the employee_id and other columns if needed
full_pdf = silver_df.toPandas()
full_pdf["predicted_score"] = pdf["predicted_score"]

# Save results back to Spark DataFrame
result_df = spark.createDataFrame(full_pdf)
result_df.write.mode("overwrite").saveAsTable("test.default.gold_ml_productivity_insights")

/databricks/python/lib/python3.12/site-packages/databricks/sdk/errors/base.py:87: UserWarning: The 'retry_after_secs' parameter of DatabricksError is deprecated and will be removed in a future version.
  warnings.warn(


In [0]:
%sql
select * from test.default.gold_ml_productivity_insights

employee_id department gender education_level productivity_score overtime_hours tenure_years remote_freq _ingested_at _source_sys predicted_score 65554 Engineering Male High School 5.0 9.0 0 25.0 2026-01-14T05:57:54.535Z Kaggle_Source 3.00247821061241 65612 Engineering Male High School 4.0 20.0 1 100.0 2026-01-14T05:57:54.535Z Kaggle_Source 2.9724021611834566 65663 Engineering Female High School 3.0 8.0 6 50.0 2026-01-14T05:57:54.535Z Kaggle_Source 3.009027827064463 65710 Engineering Female High School 4.0 21.0 2 75.0 2026-01-14T05:57:54.535Z Kaggle_Source 3.0080140929649604 65727 Engineering Male High School 3.0 4.0 1 100.0 2026-01-14T05:57:54.535Z Kaggle_Source 2.9949806192307866 65744 Engineering Male High School 1.0 15.0 8 75.0 2026-01-14T05:57:54.535Z Kaggle_Source 3.0043686317462033 65769 HR Male PhD 2.0 23.0 2 25.0 2026-01-14T05:57:54.535Z Kaggle_Source 2.9999065464022445 65821 HR Male PhD 5.0 14.0 3 0.0 2026-01-14T05:57:54.535Z Kaggle_Source 3.0051084114605295 65828 Engineering Male High School 5.0 3.0 8 100.0 2026-01-14T05:57:54.535Z Kaggle_Source 2.985101056888783 65841 Engineering Female High School 2.0 25.0 4 75.0 2026-01-14T05:57:54.535Z Kaggle_Source 3.0180831432011144 65954 Engineering Male High School 5.0 12.0 0 75.0 2026-01-14T05:57:54.535Z Kaggle_Source 2.9968254171385915 65955 Engineering Female High School 2.0 18.0 8 0.0 2026-01-14T05:57:54.535Z Kaggle_Source 3.0289989725717645 65964 Engineering Female High School 1.0 26.0 6 0.0 2026-01-14T05:57:54.535Z Kaggle_Source 3.018639055481636 65996 Engineering Female High School 3.0 9.0 3 0.0 2026-01-14T05:57:54.535Z Kaggle_Source 3.0053449718510836 65999 Engineering Female High School 1.0 19.0 7 25.0 2026-01-14T05:57:54.535Z Kaggle_Source 3.017558018153666 66008 Engineering Female High School 3.0 21.0 0 25.0 2026-01-14T05:57:54.535Z Kaggle_Source 2.9834207901197862 66026 Engineering Male High School 2.0 29.0 0 100.0 2026-01-14T05:57:54.535Z Kaggle_Source 2.9744664325883337 66089 Engineering Female High School 4.0 22.0 4 25.0 2026-01-14T05:57:54.535Z Kaggle_Source 3.0037066547187674 66099 Engineering Female High School 5.0 9.0 4 25.0 2026-01-14T05:57:54.535Z Kaggle_Source 3.0208911510038012 66105 Engineering Female High School 2.0 24.0 1 50.0 2026-01-14T05:57:54.535Z Kaggle_Source 2.9802561440947795 66108 Engineering Female High School 1.0 16.0 7 25.0 2026-01-14T05:57:54.535Z Kaggle_Source 3.0113115329287887 66133 Engineering Male High School 2.0 23.0 3 50.0 2026-01-14T05:57:54.535Z Kaggle_Source 3.009331161427528 66170 Engineering Female High School 5.0 10.0 3 0.0 2026-01-14T05:57:54.535Z Kaggle_Source 3.0039350321289238 66191 Engineering Male High School 5.0 13.0 5 100.0 2026-01-14T05:57:54.535Z Kaggle_Source 3.0168636838314455 66232 Engineering Female High School 5.0 22.0 0 100.0 2026-01-14T05:57:54.535Z Kaggle_Source 2.9890356704371834 66233 HR Male PhD 4.0 28.0 3 25.0 2026-01-14T05:57:54.535Z Kaggle_Source 2.9567021638494815 66243 Engineering Female High School 2.0 3.0 9 0.0 2026-01-14T05:57:54.535Z Kaggle_Source 2.95745411156806 66273 Engineering Female High School 3.0 12.0 8 100.0 2026-01-14T05:57:54.535Z Kaggle_Source 3.000348584134344 66280 Engineering Female High School 1.0 26.0 2 25.0 2026-01-14T05:57:54.535Z Kaggle_Source 3.02452613668267 66283 Engineering Male High School 5.0 22.0 5 100.0 2026-01-14T05:57:54.535Z Kaggle_Source 3.015265803968489 66331 Engineering Male High School 3.0 5.0 8 50.0 2026-01-14T05:57:54.535Z Kaggle_Source 2.987898950840101 66336 HR Male PhD 5.0 1.0 2 75.0 2026-01-14T05:57:54.535Z Kaggle_Source 3.021778176642492 66340 Engineering Male High School 2.0 20.0 0 25.0 2026-01-14T05:57:54.535Z Kaggle_Source 2.9834207901197862 66356 Engineering Male High School 4.0 24.0 1 50.0 2026-01-14T05:57:54.535Z Kaggle_Source 2.9802561440947795 66360 Engineering Male High School 5.0 16.0 9 50.0 2026-01-14T05:57:54.535Z Kaggle_Source 3.047420358115613 66372 Engineering Male High School 2.0 15.0 4 75.0 2026-01-14T05:57:54.535Z Kaggle_Source 3.0131

In [0]:
%sql
CREATE OR REPLACE VIEW test.default.gold_performance_insights AS
SELECT 
    e.employee_id,
    e.department,
    e.tenure_years,
    e.remote_freq,
    e.overtime_hours,
    e.productivity_score AS actual_productivity,
    m.predicted_score,
    -- Calculate the 'Model Variance' (Actual vs. Expected)
    (e.productivity_score - m.predicted_score) AS performance_gap,
    -- Categorize performance based on ML expectation
    CASE 
        WHEN (e.productivity_score - m.predicted_score) > 2 THEN 'Over-performer'
        WHEN (e.productivity_score - m.predicted_score) < -2 THEN 'Under-performer'
        ELSE 'Meeting Expectations'
    END AS ml_performance_status,
    -- Add a ranking for 'Top Talents' within each department
    RANK() OVER (PARTITION BY e.department ORDER BY e.productivity_score DESC) as dept_rank
FROM test.default.employee_performance_silver e
JOIN test.default.gold_ml_productivity_insights m ON e.employee_id = m.employee_id;

COMMENT ON TABLE test.default.gold_performance_insights IS 'Unified BI layer combining actual performance data with ML-predicted benchmarks.';

In [0]:
%sql
select * from test.default.gold_performance_insights where department='HR' limit 60 

employee_id department tenure_years remote_freq overtime_hours actual_productivity predicted_score performance_gap ml_performance_status dept_rank 40 HR 1 100.0 2.0 5.0 2.996400890750029 2.003599109249971 Meeting Expectations 1 132 HR 0 25.0 28.0 5.0 3.025912701731231 1.9740872982687692 Meeting Expectations 1 162 HR 4 0.0 20.0 5.0 2.9813237120413723 2.0186762879586277 Meeting Expectations 1 198 HR 3 75.0 22.0 5.0 3.0064540528748216 1.9935459471251784 Meeting Expectations 1 227 HR 9 25.0 18.0 5.0 3.047828726680035 1.9521712733199652 Meeting Expectations 1 245 HR 4 100.0 7.0 5.0 3.026387592044235 1.9736124079557649 Meeting Expectations 1 441 HR 7 100.0 18.0 5.0 3.024246779812416 1.9757532201875838 Meeting Expectations 1 506 HR 8 75.0 2.0 5.0 3.008266493368164 1.991733506631836 Meeting Expectations 1 583 HR 9 75.0 25.0 5.0 3.0404364345425456 1.9595635654574544 Meeting Expectations 1 612 HR 1 100.0 14.0 5.0 3.00324878278371 1.99675121721629 Meeting Expectations 1 634 HR 0 75.0 1.0 5.0 3.034341532718892 1.965658467281108 Meeting Expectations 1 747 HR 8 75.0 4.0 5.0 2.989255164584594 2.010744835415406 Meeting Expectations 1 995 HR 9 100.0 5.0 5.0 2.984517130734304 2.015482869265696 Meeting Expectations 1 1191 HR 0 75.0 2.0 5.0 3.034341532718892 1.965658467281108 Meeting Expectations 1 1481 HR 6 0.0 3.0 5.0 2.986920977494113 2.013079022505887 Meeting Expectations 1 1534 HR 3 100.0 23.0 5.0 3.007833591068951 1.9921664089310491 Meeting Expectations 1 1850 HR 0 25.0 21.0 5.0 3.0137957877313655 1.9862042122686345 Meeting Expectations 1 1875 HR 4 75.0 6.0 5.0 3.0212238959884354 1.9787761040115646 Meeting Expectations 1 2135 HR 9 25.0 3.0 5.0 2.986275180429852 2.013724819570148 Meeting Expectations 1 2160 HR 1 50.0 10.0 5.0 3.0038633543347535 1.9961366456652465 Meeting Expectations 1 2177 HR 9 100.0 3.0 5.0 2.986844015594167 2.013155984405833 Meeting Expectations 1 2194 HR 3 100.0 16.0 5.0 3.005805507968457 1.9941944920315429 Meeting Expectations 1 2196 HR 6 50.0 29.0 5.0 2.9965409663177103 2.0034590336822897 Meeting Expectations 1 2216 HR 5 50.0 24.0 5.0 3.0034820635918487 1.9965179364081513 Meeting Expectations 1 2218 HR 0 75.0 15.0 5.0 3.000854101726245 1.9991458982737549 Meeting Expectations 1 2333 HR 4 50.0 15.0 5.0 3.0201890083494383 1.9798109916505617 Meeting Expectations 1 2386 HR 4 75.0 20.0 5.0 3.002017909546562 1.997982090453438 Meeting Expectations 1 2489 HR 7 75.0 28.0 5.0 2.992858738376654 2.007141261623346 Meeting Expectations 1 2580 HR 0 0.0 4.0 5.0 3.0662449055131544 1.9337550944868456 Meeting Expectations 1 2763 HR 8 0.0 15.0 5.0 3.016654619615496 1.9833453803845038 Meeting Expectations 1 2893 HR 4 75.0 21.0 5.0 3.002017909546562 1.997982090453438 Meeting Expectations 1 2918 HR 5 75.0 21.0 5.0 2.9883449820634826 2.0116550179365174 Meeting Expectations 1 3143 HR 9 100.0 2.0 5.0 3.0083678551236774 1.9916321448763226 Meeting Expectations 1 3194 HR 9 75.0 22.0 5.0 2.993883428827379 2.006116571172621 Meeting Expectations 1 3206 HR 9 100.0 10.0 5.0 2.9873100034039535 2.0126899965960465 Meeting Expectations 1 3244 HR 5 75.0 1.0 5.0 2.988898390601359 2.011101609398641 Meeting Expectations 1 3423 HR 2 50.0 20.0 5.0 3.0077113599151146 1.9922886400848854 Meeting Expectations 1 3498 HR 4 75.0 10.0 5.0 3.014249856065863 1.985750143934137 Meeting Expectations 1 3754 HR 8 100.0 29.0 5.0 3.0320393686686744 1.9679606313313256 Meeting Expectations 1 3790 HR 1 100.0 9.0 5.0 2.989111428125021 2.010888571874979 Meeting Expectations 1 3835 HR 0 100.0 0.0 5.0 3.0247134602322028 1.9752865397677972 Meeting Expectations 1 3907 HR 0 0.0 6.0 5.0 2.996449231421358 2.003550768578642 Meeting Expectations 1 4041 HR 4 50.0 0.0 5.0 3.029402946181913 1.970597053818087 Meeting Expectations 1 4117 HR 3 75.0 28.0 5.0 3.0182515241672774 1.9817484758327226 Meeting Expectations 1 4194 HR 4 75.0 23.0 5.0 3.007833591068951 1.9921664089310491 Meeting Expectations 1 4257 HR 7 0.0 11.0 5.0 2.9844453307326613 2.0155546692673387 Meeting Expectations 1 4417 HR 6 50.0 25